In [1]:
import numpy as np

#import torch 

data = open("PatientDetect.txt", "r")

tdata = np.empty((0,24),dtype=float)
tlabel = np.empty((0,3),dtype=float)
for d in data.readlines():
    tdata = np.append(tdata, np.array([float(t) for t in d.split(",")[:24]]).reshape((1,24)), axis=0 )
    labelNum = float(d.split(",")[24].strip("\n"))
    labelV = np.zeros((3,1))
    labelV[int(labelNum)] = 1
    tlabel = np.append(tlabel, labelV.reshape(1,3), axis=0)
    
print(tdata)
print(tlabel)

[[  0.   0.   0. ... 966. 954. 958.]
 [ 15.  34.  11. ... 952. 939. 951.]
 [ 77.  19.   0. ... 944. 952. 957.]
 ...
 [ -8.  -1.   4. ... 962. 955. 959.]
 [ 36.   1.   3. ... 963. 950. 929.]
 [  9.   6.  10. ... 956. 948. 959.]]
[[1. 0. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [1. 0. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 0. 1.]
 [0. 1. 0.]
 [0. 1. 0.]
 [0.

In [8]:
#isBody predictor
import keras
import pickle
from keras.optimizers import Adam,SGD 
from keras.models import Sequential
from sklearn.model_selection import train_test_split
from keras.layers import Dense
# Neural network

X_train, x_test, y_train, y_test = train_test_split(tdata, tlabel, test_size=0.05, random_state=80)

model = Sequential()
model.add(Dense(12, input_dim=24,kernel_initializer='normal', activation='linear'))
#model.add(Dense(24, kernel_initializer='normal', activation='linear'))
model.add(Dense(6, kernel_initializer='normal',activation='linear'))
model.add(Dense(3, kernel_initializer='normal',activation='sigmoid'))
#model.add(Dense(1, kernel_initializer='normal',activation='linear'))

opt = Adam(lr=0.0001)#, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)#adam also does the same but gives better accuracy initially 90.08 or 90.11
model.compile(loss=['binary_crossentropy'], 
              optimizer=opt, 
              metrics=['accuracy'])

history = model.fit(X_train, y_train, epochs=2000,validation_split=0.2, batch_size=64)

print(model.evaluate(X_train, y_train)[1])
predictions=model.predict(tdata, batch_size=300, verbose=1)

tot = 0
corr = 0
predLabel = np.zeros((len(tlabel), 1, 3), dtype = float)
corrLabel = np.zeros((len(tlabel), 1, 3), dtype = float)
confLabel = np.zeros((len(tlabel), 1))
confPred = np.zeros((len(tlabel), 1))
print("linear linear")
for i in range(len(tlabel)):
    print(predictions[i],tlabel[i])
    #print(tlabel[i].size)
    print(".....")
    maxPos = np.argmax(predictions[i])
    #predLabel = np.zeros((1,3), dtype=float)
    #corrLabel = np.zeros((1,3), dtype=float)
    predLabel[i][0][maxPos] = 1.0
    corrLabel[i][0] = tlabel[i]
    confLabel[i] = np.argmax(tlabel[i])
    confPred[i] = np.argmax(predictions[i])
    
    if(np.array_equal(corrLabel[i], predLabel[i])):
        corr += 1
    tot += 1
    
print("Correct " + str(corr) + " , Total " + str(tot) + " , Accuracy " + str(corr/tot))
model.save('isBody_predictor.h5')

#import pandas as pd
#data = {'y_Actual':    y1.reshape(1,len(y1))[0],
#        'y_Predicted': pred#.reshape(1,len(y_test))[0]
#        }

#df = pd.DataFrame(data, columns=['y_Actual','y_Predicted'])

#confusion_matrix = pd.crosstab(df['y_Actual'], df['y_Predicted'], rownames=['Actual'], colnames=['Predicted'])
#print(confusion_matrix)



from sklearn.metrics import confusion_matrix
confusion_matrix(confLabel, confPred)




Train on 140 samples, validate on 35 samples
Epoch 1/2000
140/140 [==============================] - 0s 2ms/step - loss: 2.0585 - accuracy: 0.4762 - val_loss: 2.1287 - val_accuracy: 0.4095
Epoch 2/2000
140/140 [==============================] - 0s 136us/step - loss: 1.8651 - accuracy: 0.4762 - val_loss: 1.9179 - val_accuracy: 0.4095
Epoch 3/2000
140/140 [==============================] - 0s 93us/step - loss: 1.6766 - accuracy: 0.4762 - val_loss: 1.7176 - val_accuracy: 0.4095
Epoch 4/2000
140/140 [==============================] - 0s 143us/step - loss: 1.5089 - accuracy: 0.4762 - val_loss: 1.5301 - val_accuracy: 0.4095
Epoch 5/2000
140/140 [==============================] - 0s 121us/step - loss: 1.3461 - accuracy: 0.4762 - val_loss: 1.3581 - val_accuracy: 0.4095
Epoch 6/2000
140/140 [==============================] - 0s 93us/step - loss: 1.2030 - accuracy: 0.4762 - val_loss: 1.2008 - val_accuracy: 0.4095
Epoch 7/2000
140/140 [==============================] - 0s 157us/step - loss: 1.065

140/140 [==============================] - 0s 86us/step - loss: 0.5909 - accuracy: 0.6881 - val_loss: 0.5594 - val_accuracy: 0.7048
Epoch 57/2000
140/140 [==============================] - ETA: 0s - loss: 0.6043 - accuracy: 0.66 - 0s 100us/step - loss: 0.5900 - accuracy: 0.6976 - val_loss: 0.5580 - val_accuracy: 0.7048
Epoch 58/2000
140/140 [==============================] - 0s 93us/step - loss: 0.5891 - accuracy: 0.6952 - val_loss: 0.5567 - val_accuracy: 0.7048
Epoch 59/2000
140/140 [==============================] - 0s 86us/step - loss: 0.5889 - accuracy: 0.7000 - val_loss: 0.5556 - val_accuracy: 0.7048
Epoch 60/2000
140/140 [==============================] - 0s 93us/step - loss: 0.5880 - accuracy: 0.7024 - val_loss: 0.5543 - val_accuracy: 0.7048
Epoch 61/2000
140/140 [==============================] - ETA: 0s - loss: 0.5953 - accuracy: 0.71 - 0s 93us/step - loss: 0.5873 - accuracy: 0.7000 - val_loss: 0.5543 - val_accuracy: 0.7048
Epoch 62/2000
140/140 [==============================

140/140 [==============================] - 0s 114us/step - loss: 0.5521 - accuracy: 0.6833 - val_loss: 0.5204 - val_accuracy: 0.6857
Epoch 112/2000
140/140 [==============================] - 0s 143us/step - loss: 0.5513 - accuracy: 0.6833 - val_loss: 0.5186 - val_accuracy: 0.6857
Epoch 113/2000
140/140 [==============================] - 0s 121us/step - loss: 0.5500 - accuracy: 0.6857 - val_loss: 0.5160 - val_accuracy: 0.7048
Epoch 114/2000
140/140 [==============================] - 0s 93us/step - loss: 0.5485 - accuracy: 0.6952 - val_loss: 0.5135 - val_accuracy: 0.7143
Epoch 115/2000
140/140 [==============================] - 0s 143us/step - loss: 0.5477 - accuracy: 0.7024 - val_loss: 0.5106 - val_accuracy: 0.7238
Epoch 116/2000
140/140 [==============================] - 0s 93us/step - loss: 0.5470 - accuracy: 0.7143 - val_loss: 0.5088 - val_accuracy: 0.7429
Epoch 117/2000
140/140 [==============================] - ETA: 0s - loss: 0.5636 - accuracy: 0.70 - 0s 86us/step - loss: 0.5463 -

140/140 [==============================] - 0s 107us/step - loss: 0.4998 - accuracy: 0.7738 - val_loss: 0.4562 - val_accuracy: 0.8381
Epoch 167/2000
140/140 [==============================] - 0s 128us/step - loss: 0.4979 - accuracy: 0.8048 - val_loss: 0.4538 - val_accuracy: 0.8571
Epoch 168/2000
140/140 [==============================] - 0s 86us/step - loss: 0.4960 - accuracy: 0.8167 - val_loss: 0.4523 - val_accuracy: 0.8667
Epoch 169/2000
140/140 [==============================] - 0s 107us/step - loss: 0.4947 - accuracy: 0.8119 - val_loss: 0.4516 - val_accuracy: 0.8667
Epoch 170/2000
140/140 [==============================] - 0s 143us/step - loss: 0.4935 - accuracy: 0.8119 - val_loss: 0.4499 - val_accuracy: 0.8667
Epoch 171/2000
140/140 [==============================] - 0s 121us/step - loss: 0.4923 - accuracy: 0.8048 - val_loss: 0.4484 - val_accuracy: 0.8667
Epoch 172/2000
140/140 [==============================] - 0s 114us/step - loss: 0.4912 - accuracy: 0.8024 - val_loss: 0.4475 - v

140/140 [==============================] - 0s 93us/step - loss: 0.4351 - accuracy: 0.8476 - val_loss: 0.3865 - val_accuracy: 0.8952
Epoch 222/2000
140/140 [==============================] - 0s 93us/step - loss: 0.4342 - accuracy: 0.8524 - val_loss: 0.3832 - val_accuracy: 0.8952
Epoch 223/2000
140/140 [==============================] - 0s 86us/step - loss: 0.4331 - accuracy: 0.8429 - val_loss: 0.3821 - val_accuracy: 0.8952
Epoch 224/2000
140/140 [==============================] - 0s 86us/step - loss: 0.4322 - accuracy: 0.8476 - val_loss: 0.3809 - val_accuracy: 0.8952
Epoch 225/2000
140/140 [==============================] - 0s 121us/step - loss: 0.4310 - accuracy: 0.8476 - val_loss: 0.3802 - val_accuracy: 0.8952
Epoch 226/2000
140/140 [==============================] - 0s 93us/step - loss: 0.4298 - accuracy: 0.8476 - val_loss: 0.3795 - val_accuracy: 0.9143
Epoch 227/2000
140/140 [==============================] - 0s 121us/step - loss: 0.4282 - accuracy: 0.8548 - val_loss: 0.3787 - val_a

...

140/140 [==============================] - 0s 128us/step - loss: 0.2089 - accuracy: 0.9000 - val_loss: 0.1859 - val_accuracy: 0.9238
Epoch 1866/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2065 - accuracy: 0.9000 - val_loss: 0.1759 - val_accuracy: 0.9333
Epoch 1867/2000
140/140 [==============================] - 0s 86us/step - loss: 0.2050 - accuracy: 0.9048 - val_loss: 0.1727 - val_accuracy: 0.9429
Epoch 1868/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2080 - accuracy: 0.9119 - val_loss: 0.1719 - val_accuracy: 0.9333
Epoch 1869/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2096 - accuracy: 0.9095 - val_loss: 0.1718 - val_accuracy: 0.9429
Epoch 1870/2000
140/140 [==============================] - 0s 186us/step - loss: 0.2087 - accuracy: 0.9024 - val_loss: 0.1771 - val_accuracy: 0.9238
Epoch 1871/2000
140/140 [==============================] - 0s 128us/step - loss: 0.2034 - accuracy: 0.8952 - val_loss: 0.18

Epoch 1920/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2122 - accuracy: 0.9024 - val_loss: 0.1731 - val_accuracy: 0.9143
Epoch 1921/2000
140/140 [==============================] - ETA: 0s - loss: 0.2123 - accuracy: 0.90 - 0s 86us/step - loss: 0.2199 - accuracy: 0.9024 - val_loss: 0.1712 - val_accuracy: 0.9238
Epoch 1922/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2125 - accuracy: 0.9048 - val_loss: 0.1719 - val_accuracy: 0.9333
Epoch 1923/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2056 - accuracy: 0.9000 - val_loss: 0.1791 - val_accuracy: 0.9238
Epoch 1924/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2049 - accuracy: 0.8976 - val_loss: 0.1833 - val_accuracy: 0.9238
Epoch 1925/2000
140/140 [==============================] - 0s 128us/step - loss: 0.2061 - accuracy: 0.9000 - val_loss: 0.1823 - val_accuracy: 0.9238
Epoch 1926/2000
140/140 [==============================] - 0s 93us/s

140/140 [==============================] - 0s 121us/step - loss: 0.2065 - accuracy: 0.9024 - val_loss: 0.1806 - val_accuracy: 0.9238
Epoch 1975/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2047 - accuracy: 0.9024 - val_loss: 0.1719 - val_accuracy: 0.9333
Epoch 1976/2000
140/140 [==============================] - 0s 107us/step - loss: 0.2075 - accuracy: 0.9119 - val_loss: 0.1705 - val_accuracy: 0.9333
Epoch 1977/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2105 - accuracy: 0.9048 - val_loss: 0.1706 - val_accuracy: 0.9333
Epoch 1978/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2080 - accuracy: 0.9048 - val_loss: 0.1748 - val_accuracy: 0.9238
Epoch 1979/2000
140/140 [==============================] - 0s 93us/step - loss: 0.2038 - accuracy: 0.8905 - val_loss: 0.1824 - val_accuracy: 0.9238
Epoch 1980/2000
140/140 [==============================] - 0s 114us/step - loss: 0.2079 - accuracy: 0.9000 - val_loss: 0.1880 

[0.00072761 0.5643544  0.12922639] [0. 1. 0.]
.....
[2.5166431e-04 9.2200613e-01 2.2243071e-02] [0. 1. 0.]
.....
[2.1625683e-04 9.3092036e-01 2.5130473e-02] [0. 1. 0.]
.....
[0.00156969 0.11258861 0.5673561 ] [0. 0. 1.]
.....
[2.74593127e-04 1.02860026e-01 7.53842175e-01] [0. 0. 1.]
.....
[3.6112723e-04 2.2876745e-01 5.0390959e-01] [0. 0. 1.]
.....
[0.0005606  0.18056244 0.3779755 ] [0. 0. 1.]
.....
[2.7944901e-04 3.0365083e-01 2.7868506e-01] [0. 0. 1.]
.....
[5.1685795e-04 5.6278360e-01 1.1126759e-01] [0. 0. 1.]
.....
[2.1965748e-08 5.8656591e-01 7.7151608e-01] [0. 1. 0.]
.....
[1.4996884e-07 9.9733740e-01 6.0631894e-03] [0. 1. 0.]
.....
[9.2528541e-07 9.9129242e-01 1.7316276e-02] [0. 1. 0.]
.....
[3.0836884e-09 9.3218172e-01 4.6408257e-01] [0. 1. 0.]
.....
[4.271883e-08 9.992823e-01 3.148934e-03] [0. 1. 0.]
.....
[1.2508070e-08 9.9930787e-01 6.4313407e-03] [0. 1. 0.]
.....
[7.149362e-09 9.998275e-01 1.283910e-03] [0. 1. 0.]
.....
[1.4968393e-09 5.2704674e-01 9.1523147e-01] [0. 1. 0.]

array([[64,  1,  0],
       [ 0, 77,  7],
       [ 0, 14, 22]], dtype=int64)

In [9]:
import numpy as np
#import torch 

data = open("PatientWeight.txt", "r")

tdata = np.empty((0,25),dtype=float)
tlabel = np.empty((0,1),dtype=float)
for d in data.readlines():
    tdata = np.append(tdata, np.array([float(t) for t in d.split(",")[:25]]).reshape((1,25)), axis=0 )
    tlabel = np.append(tlabel, np.array([float(d.split(",")[25].strip("\n"))]).reshape(1,1) ,axis=0)
    
print(tdata)
print(tlabel)

[[ 15.  34.  11. ... 939. 951.   1.]
 [ 77.  19.   0. ... 952. 957.   1.]
 [ -1.  21.  48. ... 947. 937.   1.]
 ...
 [ 16.  86.   8. ... 952. 963.   2.]
 [ 17. 109.   9. ... 946. 961.   2.]
 [ 20. 103.  14. ... 947. 961.   2.]]
[[78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [78.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [40.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [56.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [48.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [72.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [55.]
 [

In [13]:
#isWeight predictor
import keras
import pickle
import tensorflow as tf
from keras.optimizers import Adam,SGD 
from keras.models import Sequential
from sklearn.model_selection import train_test_split
from keras.layers import Dense

#def L2_Loss(y_true, y_pred):
#    return tf.math_sqrt(tf.reduce_sum(tf.square(y_true - y_pred)))

# Neural network

X_train, x_test, y_train, y_test = train_test_split(tdata, tlabel, test_size=0.05, random_state=80)

print(y_train)

model = Sequential()
model.add(Dense(48, input_dim=25,kernel_initializer='normal', activation='relu'))
model.add(Dense(24, kernel_initializer='normal', activation='relu'))
model.add(Dense(12, kernel_initializer='normal',activation='relu'))
model.add(Dense(6, kernel_initializer='normal',activation='relu'))
model.add(Dense(1, kernel_initializer='normal',activation='linear'))

opt = Adam(lr=0.001)#, beta_1=0.9, beta_2=0.999, epsilon=None, decay=0.0, amsgrad=False)#adam also does the same but gives better accuracy initially 90.08 or 90.11
model.compile(loss="MSE", 
              optimizer=opt, 
              metrics=['accuracy'])

history = model.fit(X_train, y_train, epochs=50000,validation_split=0.2, batch_size=64)

print(model.evaluate(X_train, y_train)[1])
predictions=model.predict(tdata, batch_size=300, verbose=1)

tot = 0
corr = 0
print("linear linear")
for i in range(len(tlabel)):
    print(predictions[i][0],tlabel[i][0])
    #if(abs(int(predictions[i][0]) - int(tlabel[i][0])) <= 5):
    #    corr += 1
    percent = predictions[i][0] * 0.1
    if(abs(predictions[i][0] + percent) >= tlabel[i] and abs(predictions[i][0] - percent) <= tlabel[i]):
        corr += 1
    tot += 1
    
print("Correct " + str(corr) + " , Total " + str(tot) + " , Accuracy " + str(corr/tot))
model.save('isBodyWeigth_predictor.h5')

[[48.]
 [40.]
 [48.]
 [72.]
 [55.]
 [48.]
 [78.]
 [55.]
 [48.]
 [72.]
 [72.]
 [56.]
 [55.]
 [55.]
 [40.]
 [40.]
 [56.]
 [72.]
 [72.]
 [78.]
 [40.]
 [72.]
 [56.]
 [40.]
 [40.]
 [55.]
 [48.]
 [78.]
 [56.]
 [72.]
 [56.]
 [78.]
 [56.]
 [78.]
 [72.]
 [55.]
 [56.]
 [78.]
 [40.]
 [48.]
 [40.]
 [56.]
 [72.]
 [56.]
 [40.]
 [72.]
 [48.]
 [78.]
 [40.]
 [40.]
 [48.]
 [56.]
 [48.]
 [56.]
 [48.]
 [48.]
 [55.]
 [56.]
 [72.]
 [55.]
 [78.]
 [72.]
 [40.]
 [40.]
 [48.]
 [72.]
 [72.]
 [48.]
 [72.]
 [40.]
 [40.]
 [56.]
 [78.]
 [56.]
 [78.]
 [78.]
 [55.]
 [40.]
 [55.]
 [56.]
 [55.]
 [55.]
 [40.]
 [55.]
 [55.]
 [56.]
 [48.]
 [78.]
 [48.]
 [78.]
 [72.]
 [48.]
 [40.]
 [55.]
 [55.]
 [56.]
 [78.]
 [56.]
 [72.]
 [78.]
 [55.]
 [48.]
 [78.]
 [72.]
 [78.]
 [40.]
 [72.]
 [78.]
 [56.]
 [78.]
 [72.]
 [40.]
 [48.]
 [56.]]
Train on 91 samples, validate on 23 samples
Epoch 1/50000
91/91 [==============================] - 0s 4ms/step - loss: 3473.8717 - accuracy: 0.0000e+00 - val_loss: 3931.0808 - val_accuracy: 0.0000e+00


91/91 [==============================] - 0s 88us/step - loss: 176.7574 - accuracy: 0.0000e+00 - val_loss: 186.4791 - val_accuracy: 0.0000e+00
Epoch 48/50000
91/91 [==============================] - 0s 88us/step - loss: 175.7997 - accuracy: 0.0000e+00 - val_loss: 187.6121 - val_accuracy: 0.0000e+00
Epoch 49/50000
91/91 [==============================] - 0s 88us/step - loss: 173.9012 - accuracy: 0.0000e+00 - val_loss: 190.5038 - val_accuracy: 0.0000e+00
Epoch 50/50000
91/91 [==============================] - 0s 88us/step - loss: 171.5795 - accuracy: 0.0000e+00 - val_loss: 194.7876 - val_accuracy: 0.0000e+00
Epoch 51/50000
91/91 [==============================] - 0s 176us/step - loss: 171.3536 - accuracy: 0.0000e+00 - val_loss: 199.4888 - val_accuracy: 0.0000e+00
Epoch 52/50000
91/91 [==============================] - 0s 264us/step - loss: 169.8746 - accuracy: 0.0000e+00 - val_loss: 202.8408 - val_accuracy: 0.0000e+00
Epoch 53/50000
91/91 [==============================] - 0s 88us/step - 

91/91 [==============================] - 0s 176us/step - loss: 164.7978 - accuracy: 0.0000e+00 - val_loss: 187.6005 - val_accuracy: 0.0000e+00
Epoch 100/50000
91/91 [==============================] - 0s 176us/step - loss: 164.6893 - accuracy: 0.0000e+00 - val_loss: 186.0438 - val_accuracy: 0.0000e+00
Epoch 101/50000
91/91 [==============================] - 0s 176us/step - loss: 165.2247 - accuracy: 0.0000e+00 - val_loss: 184.9446 - val_accuracy: 0.0000e+00
Epoch 102/50000
91/91 [==============================] - 0s 176us/step - loss: 164.9023 - accuracy: 0.0000e+00 - val_loss: 185.6960 - val_accuracy: 0.0000e+00
Epoch 103/50000
91/91 [==============================] - 0s 176us/step - loss: 164.4702 - accuracy: 0.0000e+00 - val_loss: 185.9907 - val_accuracy: 0.0000e+00
Epoch 104/50000
91/91 [==============================] - 0s 176us/step - loss: 164.3341 - accuracy: 0.0000e+00 - val_loss: 186.6962 - val_accuracy: 0.0000e+00
Epoch 105/50000
91/91 [==============================] - 0s 17

Epoch 151/50000
91/91 [==============================] - 0s 176us/step - loss: 158.5757 - accuracy: 0.0000e+00 - val_loss: 171.9145 - val_accuracy: 0.0000e+00
Epoch 152/50000
91/91 [==============================] - 0s 176us/step - loss: 159.1646 - accuracy: 0.0000e+00 - val_loss: 171.8648 - val_accuracy: 0.0000e+00
Epoch 153/50000
91/91 [==============================] - 0s 176us/step - loss: 158.5955 - accuracy: 0.0000e+00 - val_loss: 171.2145 - val_accuracy: 0.0000e+00
Epoch 154/50000
91/91 [==============================] - 0s 176us/step - loss: 158.2581 - accuracy: 0.0000e+00 - val_loss: 172.6703 - val_accuracy: 0.0000e+00
Epoch 155/50000
91/91 [==============================] - 0s 176us/step - loss: 157.6685 - accuracy: 0.0000e+00 - val_loss: 175.6438 - val_accuracy: 0.0000e+00
Epoch 156/50000
91/91 [==============================] - 0s 264us/step - loss: 157.4351 - accuracy: 0.0000e+00 - val_loss: 178.4290 - val_accuracy: 0.0000e+00
Epoch 157/50000
91/91 [=======================

Epoch 203/50000
91/91 [==============================] - ETA: 0s - loss: 149.9692 - accuracy: 0.0000e+ - 0s 88us/step - loss: 150.2329 - accuracy: 0.0000e+00 - val_loss: 159.9631 - val_accuracy: 0.0000e+00
Epoch 204/50000
91/91 [==============================] - 0s 88us/step - loss: 150.5531 - accuracy: 0.0000e+00 - val_loss: 158.3557 - val_accuracy: 0.0000e+00
Epoch 205/50000
91/91 [==============================] - 0s 88us/step - loss: 151.1290 - accuracy: 0.0000e+00 - val_loss: 156.9045 - val_accuracy: 0.0000e+00
Epoch 206/50000
91/91 [==============================] - 0s 88us/step - loss: 151.2512 - accuracy: 0.0000e+00 - val_loss: 157.6821 - val_accuracy: 0.0000e+00
Epoch 207/50000
91/91 [==============================] - 0s 88us/step - loss: 150.7217 - accuracy: 0.0000e+00 - val_loss: 159.4682 - val_accuracy: 0.0000e+00
Epoch 208/50000
91/91 [==============================] - 0s 88us/step - loss: 149.6161 - accuracy: 0.0000e+00 - val_loss: 161.2100 - val_accuracy: 0.0000e+00
Epoc

...

91/91 [==============================] - 0s 88us/step - loss: 0.0992 - accuracy: 0.8901 - val_loss: 75.8596 - val_accuracy: 0.0000e+00
Epoch 49785/50000
91/91 [==============================] - 0s 176us/step - loss: 0.1335 - accuracy: 0.8352 - val_loss: 76.9256 - val_accuracy: 0.0000e+00
Epoch 49786/50000
91/91 [==============================] - 0s 176us/step - loss: 0.1336 - accuracy: 0.8571 - val_loss: 75.2930 - val_accuracy: 0.0000e+00
Epoch 49787/50000
91/91 [==============================] - 0s 176us/step - loss: 0.1067 - accuracy: 0.9121 - val_loss: 76.5466 - val_accuracy: 0.0000e+00
Epoch 49788/50000
91/91 [==============================] - 0s 176us/step - loss: 0.1012 - accuracy: 0.8681 - val_loss: 74.7909 - val_accuracy: 0.0000e+00
Epoch 49789/50000
91/91 [==============================] - 0s 88us/step - loss: 0.1134 - accuracy: 0.8791 - val_loss: 75.9314 - val_accuracy: 0.0000e+00
Epoch 49790/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0972 - accurac

91/91 [==============================] - 0s 88us/step - loss: 0.1193 - accuracy: 0.8462 - val_loss: 75.9648 - val_accuracy: 0.0000e+00
Epoch 49838/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0672 - accuracy: 0.9121 - val_loss: 77.1833 - val_accuracy: 0.0000e+00
Epoch 49839/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0733 - accuracy: 0.9121 - val_loss: 76.0618 - val_accuracy: 0.0000e+00
Epoch 49840/50000
91/91 [==============================] - 0s 176us/step - loss: 0.0714 - accuracy: 0.9121 - val_loss: 76.0210 - val_accuracy: 0.0000e+00
Epoch 49841/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0707 - accuracy: 0.9231 - val_loss: 76.7422 - val_accuracy: 0.0000e+00
Epoch 49842/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0770 - accuracy: 0.9231 - val_loss: 77.1868 - val_accuracy: 0.0000e+00
Epoch 49843/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0907 - accuracy: 

Epoch 49891/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0932 - accuracy: 0.9231 - val_loss: 75.2798 - val_accuracy: 0.0000e+00
Epoch 49892/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0910 - accuracy: 0.9011 - val_loss: 76.9288 - val_accuracy: 0.0000e+00
Epoch 49893/50000
91/91 [==============================] - 0s 88us/step - loss: 0.0795 - accuracy: 0.9121 - val_loss: 75.0284 - val_accuracy: 0.0000e+00
Epoch 49894/50000
91/91 [==============================] - 0s 176us/step - loss: 0.0854 - accuracy: 0.9011 - val_loss: 77.7359 - val_accuracy: 0.0000e+00
Epoch 49895/50000
91/91 [==============================] - 0s 88us/step - loss: 0.1522 - accuracy: 0.8242 - val_loss: 77.6216 - val_accuracy: 0.0000e+00
Epoch 49896/50000
91/91 [==============================] - 0s 88us/step - loss: 0.1257 - accuracy: 0.8571 - val_loss: 74.1348 - val_accuracy: 0.0000e+00
Epoch 49897/50000
91/91 [==============================] - 0s 88us/step - loss: 0

Epoch 49945/50000
91/91 [==============================] - 0s 88us/step - loss: 1.7957 - accuracy: 0.3626 - val_loss: 74.5306 - val_accuracy: 0.0435
Epoch 49946/50000
91/91 [==============================] - 0s 88us/step - loss: 1.0619 - accuracy: 0.2637 - val_loss: 79.5228 - val_accuracy: 0.0000e+00
Epoch 49947/50000
91/91 [==============================] - 0s 88us/step - loss: 0.6825 - accuracy: 0.2747 - val_loss: 75.8144 - val_accuracy: 0.0000e+00
Epoch 49948/50000
91/91 [==============================] - 0s 88us/step - loss: 0.5293 - accuracy: 0.5055 - val_loss: 79.2187 - val_accuracy: 0.0000e+00
Epoch 49949/50000
91/91 [==============================] - 0s 88us/step - loss: 1.2751 - accuracy: 0.4835 - val_loss: 71.5361 - val_accuracy: 0.0000e+00
Epoch 49950/50000
91/91 [==============================] - 0s 88us/step - loss: 1.1030 - accuracy: 0.3297 - val_loss: 76.4167 - val_accuracy: 0.0000e+00
Epoch 49951/50000
91/91 [==============================] - 0s 88us/step - loss: 0.2599

91/91 [==============================] - 0s 176us/step - loss: 1.5344 - accuracy: 0.2088 - val_loss: 87.1176 - val_accuracy: 0.0435
Epoch 49999/50000
91/91 [==============================] - 0s 176us/step - loss: 1.8308 - accuracy: 0.2747 - val_loss: 75.9448 - val_accuracy: 0.0435
Epoch 50000/50000
114/114 [==============================] - 0s 70us/step
0.08771929889917374
120/120 [==============================] - 0s 200us/step
linear linear
76.03116 78.0
76.6862 78.0
77.06772 78.0
64.97617 78.0
69.11279 78.0
81.27602 78.0
76.19601 78.0
76.72764 78.0
77.73886 78.0
74.47616 78.0
78.61487 78.0
76.04257 78.0
77.56215 78.0
76.67738 78.0
75.63796 78.0
67.823586 78.0
75.79629 78.0
76.905045 78.0
77.26885 78.0
77.21097 78.0
37.55712 40.0
39.521046 40.0
39.71984 40.0
41.20053 40.0
38.503414 40.0
39.254562 40.0
39.26857 40.0
38.27355 40.0
39.68595 40.0
39.304443 40.0
39.24797 40.0
38.978573 40.0
39.655613 40.0
37.835495 40.0
37.743557 40.0
39.44267 40.0
37.919518 40.0
38.76666 40.0
61.567413 4